In [1]:
#import the necessary libararies for this project
import numpy as np
import pandas as pd
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

!conda install -c conda-forge geopy --yes
from geopy.geocoders import Nominatim
import urllib.request
import json
from urllib.request import urlopen
import requests
from pandas.io.json import json_normalize

import matplotlib.cm as cm
import matplotlib.colors as colors
# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.pyplot as plt
import matplotlib.colors as colors
%matplotlib inline
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes
import folium

print('Libraries imported.')

Solving environment: done

## Package Plan ##

  environment location: /home/jupyterlab/conda/envs/python

  added / updated specs:
    - geopy


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    ca-certificates-2021.5.30  |       ha878542_0         136 KB  conda-forge
    certifi-2021.5.30          |   py36h5fab9bb_0         141 KB  conda-forge
    geographiclib-1.52         |     pyhd8ed1ab_0          35 KB  conda-forge
    geopy-2.1.0                |     pyhd3deb0d_0          64 KB  conda-forge
    ------------------------------------------------------------
                                           Total:         376 KB

The following NEW packages will be INSTALLED:

  geographiclib      conda-forge/noarch::geographiclib-1.52-pyhd8ed1ab_0
  geopy              conda-forge/noarch::geopy-2.1.0-pyhd3deb0d_0

The following packages will be UPDATED:

  ca-certificates    pkgs/main::ca-cert

In [2]:
#Read and load the json data
with open ('nyu-2451-34572-geojson.json') as json_data:
    new_york_data = json.load(json_data)

In [3]:
neighborhoods_data = new_york_data['features']
# define the dataframe columns
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 

# instantiate the dataframe
neighborhoods = pd.DataFrame(columns=column_names)

for data in neighborhoods_data:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    neighborhoods = neighborhoods.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)

In [4]:
#check the number of neighborhoods and boroughs the dataframe contains
print('The dataframe has {} boroughs and {} neighborhoods.'.format(
        len(neighborhoods['Borough'].unique()),
        neighborhoods.shape[0]
    )
)

The dataframe has 5 boroughs and 306 neighborhoods.


In [5]:
neighborhoods.head()

Borough Neighborhood   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201
1   Bronx   Co-op City  40.874294 -73.829939
2   Bronx  Eastchester  40.887556 -73.827806
3   Bronx    Fieldston  40.895437 -73.905643
4   Bronx    Riverdale  40.890834 -73.912585

In [6]:

address = 'New York City, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpHical coordinate of New York City are {}, {}.'.format(latitude, longitude))

The geograpHical coordinate of New York City are 40.7127281, -74.0060152.


In [7]:
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Borough'], neighborhoods['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=3.5,
        popup=label,
        color='green',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_newyork)  
    
map_newyork

## USING BROOKLYN AS MY CHOICE OF NEIGHBORHOOD TO EXPLORE

In [8]:
brooklyn_data = neighborhoods[neighborhoods['Borough'] == 'Brooklyn'].reset_index(drop=True)
brooklyn_data.head()

Borough Neighborhood   Latitude  Longitude
0  Brooklyn    Bay Ridge  40.625801 -74.030621
1  Brooklyn  Bensonhurst  40.611009 -73.995180
2  Brooklyn  Sunset Park  40.645103 -74.010316
3  Brooklyn   Greenpoint  40.730201 -73.954241
4  Brooklyn    Gravesend  40.595260 -73.973471

In [9]:
brooklyn_data.loc[2, 'Neighborhood']

'Sunset Park'

In [10]:
#getting the longitude and latitude of Sunset park as i want to explore locations and venues close to it.

neighborhood_latitude = brooklyn_data.loc[2, 'Latitude'] # neighborhood latitude value
neighborhood_longitude = brooklyn_data.loc[2, 'Longitude'] # neighborhood longitude value

neighborhood_name = brooklyn_data.loc[2, 'Neighborhood'] # neighborhood name

print('Latitude and longitude values of {} are {}, {}.'.format(neighborhood_name, 
                                                               neighborhood_latitude, 
                                                               neighborhood_longitude))

Latitude and longitude values of Sunset Park are 40.64510294925429, -74.01031618527784.


In [11]:

CLIENT_ID = 'O3X2YPNHOZWVQKI5NSN5UDRNQQYJLAACZJUCWS5MIEMFVGUJ' # your Foursquare ID
CLIENT_SECRET = 'HCT1WNBGLIMXVV1CEUYMP41DQUS5GRZLPPGXHDHAU1BLKEK3' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version
LIMIT = 100 # A default Foursquare API limit value

print('Your credentials:')
print('CLIENT_ID: ' + 'O3X2YPNHOZWVQKI5NSN5UDRNQQYJLAACZJUCWS5MIEMFVGUJ')
print('CLIENT_SECRET:' + 'RLDSLYXBS1K0LFZA4GRYIOTO3RUP5OAOR2BEMQ2A3QGPTOVB')

Your credentials:
CLIENT_ID: O3X2YPNHOZWVQKI5NSN5UDRNQQYJLAACZJUCWS5MIEMFVGUJ
CLIENT_SECRET:RLDSLYXBS1K0LFZA4GRYIOTO3RUP5OAOR2BEMQ2A3QGPTOVB


In [12]:
radius = 500 # define radius
LIMIT = 100 # limit of number of venues returned by Foursquare API
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    neighborhood_latitude, 
    neighborhood_longitude, 
    radius, 
    LIMIT)
url # display URL

'https://api.foursquare.com/v2/venues/explore?&client_id=O3X2YPNHOZWVQKI5NSN5UDRNQQYJLAACZJUCWS5MIEMFVGUJ&client_secret=HCT1WNBGLIMXVV1CEUYMP41DQUS5GRZLPPGXHDHAU1BLKEK3&v=20180605&ll=40.64510294925429,-74.01031618527784&radius=500&limit=100'

In [13]:
results = requests.get(url).json()

In [14]:
#A function that generates neighborhoods in  New york
def getNearbyVenues(names, latitudes, longitudes, radius=600):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
            
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
              v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [15]:
brooklyn_venues = getNearbyVenues(names=brooklyn_data['Neighborhood'],
                                   latitudes=brooklyn_data['Latitude'],
                                   longitudes=brooklyn_data['Longitude']
                                  )

Bay Ridge
Bensonhurst
Sunset Park
Greenpoint
Gravesend
Brighton Beach
Sheepshead Bay
Manhattan Terrace
Flatbush
Crown Heights
East Flatbush
Kensington
Windsor Terrace
Prospect Heights
Brownsville
Williamsburg
Bushwick
Bedford Stuyvesant
Brooklyn Heights
Cobble Hill
Carroll Gardens
Red Hook
Gowanus
Fort Greene
Park Slope
Cypress Hills
East New York
Starrett City
Canarsie
Flatlands
Mill Island
Manhattan Beach
Coney Island
Bath Beach
Borough Park
Dyker Heights
Gerritsen Beach
Marine Park
Clinton Hill
Sea Gate
Downtown
Boerum Hill
Prospect Lefferts Gardens
Ocean Hill
City Line
Bergen Beach
Midwood
Prospect Park South
Georgetown
East Williamsburg
North Side
South Side
Ocean Parkway
Fort Hamilton
Ditmas Park
Wingate
Rugby
Remsen Village
New Lots
Paerdegat Basin
Mill Basin
Fulton Ferry
Vinegar Hill
Weeksville
Broadway Junction
Dumbo
Homecrest
Highland Park
Madison
Erasmus


In [16]:
#putting the neighborhoods into a dataframe 
print(brooklyn_venues.shape)
brooklyn_venues.head()

(3209, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0    Bay Ridge              40.625801              -74.030621   
1    Bay Ridge              40.625801              -74.030621   
2    Bay Ridge              40.625801              -74.030621   
3    Bay Ridge              40.625801              -74.030621   
4    Bay Ridge              40.625801              -74.030621   

                            Venue  Venue Latitude  Venue Longitude  \
0     Pilo Arts Day Spa and Salon       40.624748       -74.030591   
1                       Bagel Boy       40.627896       -74.029335   
2  Georgian Dream Cafe and Bakery       40.625586       -74.030196   
3             Leo's Casa Calamari       40.624200       -74.030931   
4                    Pegasus Cafe       40.623168       -74.031186   

         Venue Category  
0                   Spa  
1            Bagel Shop  
2  Caucasian Restaurant  
3           Pizza Place  
4        Breakfast Spot

In [17]:
#Grouping the rows by neighborhood and taking the mean of the frequency of each occurence
brooklyn_onehot = pd.get_dummies(brooklyn_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
brooklyn_onehot['Neighborhoods'] = brooklyn_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [brooklyn_onehot.columns[-1]] + list(brooklyn_onehot.columns[:-1])
brooklyn_onehot =brooklyn_onehot[fixed_columns]

brooklyn_onehot.head()

Neighborhoods  Adult Boutique  Airport Terminal  American Restaurant  \
0     Bay Ridge               0                 0                    0   
1     Bay Ridge               0                 0                    0   
2     Bay Ridge               0                 0                    0   
3     Bay Ridge               0                 0                    0   
4     Bay Ridge               0                 0                    0   

   Animal Shelter  Antique Shop  Arepa Restaurant  Argentinian Restaurant  \
0               0             0                 0                       0   
1               0             0                 0                       0   
2               0             0                 0                       0   
3               0             0                 0                       0   
4               0             0                 0                       0   

   Art Gallery  Arts & Crafts Store  Arts & Entertainment  Asian Restaurant  \
0            0                    0                     0                 0   
1            0                    0                     0                 0   
2            0                    0                     0                 0   
3            0                    0                     0                 0   
4            0                    0                     0                 0   

   Athletics & Sports  Auto Dealership  Auto Garage  BBQ Joint  Bagel Shop  \
0                   0                0            0          0           0   
1                   0                0            0          0           1   
2                   0                0            0          0           0   
3                   0                0            0          0           0   
4                   0                0            0          0           0   

   Bakery  Bank  Bar  Baseball Field  Baseball Stadium  Basketball Court  \
0       0     0    0               0                 0                 0   
1       0     0    0               0                 0                 0   
2       0     0    0               0                 0                 0   
3       0     0    0               0                 0                 0   
4       0     0    0               0                 0                 0   

   Bath House  Beach  Beer Bar  Beer Garden  Beer Store  \
0           0      0         0            0           0   
1           0      0         0            0           0   
2           0      0         0            0           0   
3           0      0         0            0           0   
4           0      0         0            0           0   

   Bike Rental / Bike Share  Bike Shop  Bike Trail  Bistro  Board Shop  \
0                         0          0           0       0           0   
1                         0          0           0       0           0   
2                         0          0           0       0           0   
3                         0          0           0       0           0   
4                         0          0           0       0           0   

   Boat or Ferry  Bookstore  Boutique  Boxing Gym  Brazilian Restaurant  \
0              0          0         0           0                     0   
1              0          0         0           0                     0   
2              0          0         0           0                     0   
3              0          0         0           0                     0   
4              0          0         0           0                     0   

   Breakfast Spot  Brewery  Bridal Shop  Bridge  Bubble Tea Shop  Buffet  \
0               0        0            0       0                0       0   
1               0        0            0       0                0       0   
2               0        0            0       0                0       0   
3               0        0            0       0                0       0   
4               1        0            0       0               

In [18]:
#Grouping the data by neighborhood 
brooklyn_grouped = brooklyn_onehot.groupby('Neighborhoods').mean().reset_index()
brooklyn_grouped

Neighborhoods  Adult Boutique  Airport Terminal  \
0                  Bath Beach            0.00          0.000000   
1                   Bay Ridge            0.00          0.000000   
2          Bedford Stuyvesant            0.00          0.000000   
3                 Bensonhurst            0.00          0.000000   
4                Bergen Beach            0.00          0.000000   
5                 Boerum Hill            0.00          0.000000   
6                Borough Park            0.00          0.000000   
7              Brighton Beach            0.00          0.000000   
8           Broadway Junction            0.00          0.000000   
9            Brooklyn Heights            0.00          0.000000   
10                Brownsville            0.00          0.033333   
11                   Bushwick            0.00          0.000000   
12                   Canarsie            0.00          0.000000   
13            Carroll Gardens            0.00          0.000000   
14                  City Line            0.00          0.000000   
15               Clinton Hill            0.00          0.000000   
16                Cobble Hill            0.00          0.000000   
17               Coney Island            0.00          0.000000   
18              Crown Heights            0.00          0.000000   
19              Cypress Hills            0.00          0.000000   
20                Ditmas Park            0.00          0.000000   
21                   Downtown            0.00          0.000000   
22                      Dumbo            0.00          0.000000   
23              Dyker Heights            0.00          0.000000   
24              East Flatbush            0.00          0.000000   
25              East New York            0.00          0.000000   
26          East Williamsburg            0.00          0.000000   
27                    Erasmus            0.00          0.000000   
28                   Flatbush            0.00          0.000000   
29                  Flatlands            0.00          0.000000   
30                Fort Greene            0.00          0.000000   
31              Fort Hamilton            0.00          0.000000   
32               Fulton Ferry            0.00          0.000000   
33                 Georgetown            0.00          0.000000   
34            Gerritsen Beach            0.00          0.000000   
35                    Gowanus            0.00          0.000000   
36                  Gravesend            0.00          0.000000   
37                 Greenpoint            0.00          0.000000   
38              Highland Park            0.00          0.000000   
39                  Homecrest            0.00          0.000000   
40                 Kensington            0.00          0.000000   
41                    Madison            0.00          0.000000   
42            Manhattan Beach            0.00          0.000000   
43          Manhattan Terrace            0.00          0.000000   
44                Marine Park            0.00          0.000000   
45                    Midwood            0.00          0.000000   
46                 Mill Basin            0.00          0.000000   
47                Mill Island            0.00          0.000000   
48                   New Lots            0.00          0.000000   
49                 North Side            0.00          0.000000   
50                 Ocean Hill            0.00          0.000000   
51              Ocean Parkway            0.00          0.000000   
52            Paerdegat Basin            0.00          0.000000   
53                 Park Slope            0.00          0.000000   
54           Prospect Heights            0.00          0.000000   
55  Prospect Lefferts Gardens            0.00          0.000000   
56        Prospect Park South            0.00          0.000000   
57                   Red Hook            0.00          0.000000   
58             Remsen Village            0.00          0.000000

In [19]:
"Italian Restaurant" in brooklyn_venues['Venue Category'].unique()

True

In [20]:
#Neighborhoods with the top 3 most common venues
num_top_venues = 3

for hood in brooklyn_grouped['Neighborhoods']:
    print("----"+hood+"----")
    temp = brooklyn_grouped[brooklyn_grouped['Neighborhoods'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Bath Beach----
         venue  freq
0         Bank  0.08
1  Pizza Place  0.07
2     Pharmacy  0.05


----Bay Ridge----
                venue  freq
0         Pizza Place  0.06
1  Italian Restaurant  0.05
2      Cosmetics Shop  0.05


----Bedford Stuyvesant----
         venue  freq
0  Coffee Shop  0.13
1          Bar  0.07
2  Pizza Place  0.07


----Bensonhurst----
                venue  freq
0              Bakery   0.1
1          Donut Shop   0.1
2  Italian Restaurant   0.1


----Bergen Beach----
             venue  freq
0  Harbor / Marina  0.25
1       Playground  0.25
2   Baseball Field  0.12


----Boerum Hill----
                 venue  freq
0          Coffee Shop  0.06
1                  Bar  0.05
2  Arts & Crafts Store  0.04


----Borough Park----
        venue  freq
0        Bank  0.15
1        Café  0.12
2  Kids Store  0.08


----Brighton Beach----
                venue  freq
0  Russian Restaurant  0.08
1               Beach  0.06
2         Supermarket  0.04


----Broadway Ju

In [21]:
len(brooklyn_grouped[brooklyn_grouped["Italian Restaurant"] > 0])

30

In [22]:
#dataframe of italian restaurants in the nighborhood
american_r = brooklyn_grouped[["Neighborhoods","American Restaurant"]]
american_r.head()

Neighborhoods  American Restaurant
0          Bath Beach             0.000000
1           Bay Ridge             0.020619
2  Bedford Stuyvesant             0.021739
3         Bensonhurst             0.000000
4        Bergen Beach             0.000000

In [23]:
kclusters =4

brooklyn_grouped_clustering = brooklyn_grouped.drop('Neighborhoods', 1 )

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(brooklyn_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([3, 0, 0, 0, 0, 0, 3, 0, 3, 0], dtype=int32)

In [24]:
brooklyn_merged = american_r.copy()

# add clustering labels
brooklyn_merged["Cluster Labels"] = kmeans.labels_

In [42]:

brooklyn_merged.rename(columns={"Neighborhoods": "Neighborhood"}, inplace=True)
brooklyn_merged.head(5)

Neighborhood  American Restaurant  Cluster Labels  Neighborhood Latitude  \
0   Bath Beach                  0.0               3              40.599519   
0   Bath Beach                  0.0               3              40.599519   
0   Bath Beach                  0.0               3              40.599519   
0   Bath Beach                  0.0               3              40.599519   
0   Bath Beach                  0.0               3              40.599519   

   Neighborhood Longitude                    Venue  Venue Latitude  \
0              -73.998752                   Carvel       40.598733   
0              -73.998752        Pino's Ristorante       40.600955   
0              -73.998752  Bay Parkway Water Front       40.595941   
0              -73.998752                Five Guys       40.595236   
0              -73.998752                 Delacqua       40.604216   

   Venue Longitude      Venue Category  
0       -73.997670      Ice Cream Shop  
0       -74.000806  Italian Restaurant  
0       -74.000917           Surf Spot  
0       -74.000225        Burger Joint  
0       -73.997452                 Spa

In [26]:

brooklyn_merged = brooklyn_merged.join(brooklyn_venues.set_index("Neighborhood"), on="Neighborhood")

brooklyn_merged.head()

Neighborhood  American Restaurant  Cluster Labels  Neighborhood Latitude  \
0   Bath Beach                  0.0               3              40.599519   
0   Bath Beach                  0.0               3              40.599519   
0   Bath Beach                  0.0               3              40.599519   
0   Bath Beach                  0.0               3              40.599519   
0   Bath Beach                  0.0               3              40.599519   

   Neighborhood Longitude                    Venue  Venue Latitude  \
0              -73.998752                   Carvel       40.598733   
0              -73.998752        Pino's Ristorante       40.600955   
0              -73.998752  Bay Parkway Water Front       40.595941   
0              -73.998752                Five Guys       40.595236   
0              -73.998752                 Delacqua       40.604216   

   Venue Longitude      Venue Category  
0       -73.997670      Ice Cream Shop  
0       -74.000806  Italian Restaurant  
0       -74.000917           Surf Spot  
0       -74.000225        Burger Joint  
0       -73.997452                 Spa

In [28]:
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=10, tiles='Mapbox Bright')

# set color scheme for the clusters


# add markers to the map
markers_colors={}
markers_colors[0] = 'red'
markers_colors[1] = 'blue'
markers_colors[2] = 'green'
markers_colors[3] = 'yellow'
markers_colors[4] = 'purple'
markers_colors[5] = 'black'
for lat, lon, cluster in zip(brooklyn_merged['Neighborhood Latitude'], brooklyn_merged['Neighborhood Longitude'], brooklyn_merged['Cluster Labels']):
    
    
    folium.features.CircleMarker(
        [lat, lon],
        radius=5,
       
        color =markers_colors[cluster],
        fill_color=markers_colors[cluster],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [29]:
#cluster 0
brooklyn_merged.loc[(brooklyn_merged['Cluster Labels'] ==0) & (brooklyn_merged['Venue Category'] == 'American Restaurant') ]

Neighborhood  American Restaurant  Cluster Labels  \
1                   Bay Ridge             0.020619               0   
1                   Bay Ridge             0.020619               0   
2          Bedford Stuyvesant             0.021739               0   
5                 Boerum Hill             0.010000               0   
9            Brooklyn Heights             0.010000               0   
11                   Bushwick             0.011236               0   
16                Cobble Hill             0.010000               0   
22                      Dumbo             0.037975               0   
22                      Dumbo             0.037975               0   
22                      Dumbo             0.037975               0   
31              Fort Hamilton             0.017241               0   
32               Fulton Ferry             0.032787               0   
32               Fulton Ferry             0.032787               0   
35                    Gowanus             0.020000               0   
37                 Greenpoint             0.010000               0   
49                 North Side             0.020000               0   
49                 North Side             0.020000               0   
53                 Park Slope             0.034884               0   
53                 Park Slope             0.034884               0   
53                 Park Slope             0.034884               0   
55  Prospect Lefferts Gardens             0.012500               0   
57                   Red Hook             0.037037               0   
57                   Red Hook             0.037037               0   
60                   Sea Gate             0.076923               0   
61             Sheepshead Bay             0.023256               0   
62                 South Side             0.050000               0   
62                 South Side             0.050000               0   
62                 South Side             0.050000               0   
62                 South Side             0.050000               0   
62                 South Side             0.050000               0   
65               Vinegar Hill             0.047619               0   
65               Vinegar Hill             0.047619               0   
68            Windsor Terrace             0.028571               0   

    Neighborhood Latitude  Neighborhood Longitude  \
1               40.625801              -74.030621   
1               40.625801              -74.030621   
2               40.687232              -73.941785   
5               40.685683              -73.983748   
9               40.695864              -73.993782   
11              40.698116              -73.925258   
16              40.687920              -73.998561   
22              40.703176              -73.988753   
22              40.703176              -73.988753   
22              40.703176              -73.988753   
31              40.614768              -74.031979   
32              40.703281              -73.995508   
32              40.703281              -73.995508   
35              40.673931              -73.994441   
37              40.730201              -73.954241   
49              40.714823              -73.958809   
49              40.714823              -73.958809   
53              40.672321              -73.977050   
53              40.672321              -73.977050   
53              40.672321              -73.977050   
55              40.658420              -73.954899   
57              40.676253              -74.012759   
57              40.676253              -74.012759   
60              40.576375              -74.007873   
61              40.586890              -73.943186   
62              40.710861              -73.958001   
62              40.710861              -73.958001   
62              40.710861              -73.958001   
62              40.710861              -73.958001   
62              40.710861              -73.958

In [30]:
#cluster 1
brooklyn_merged.loc[(brooklyn_merged['Cluster Labels'] ==1) & (brooklyn_merged['Venue Category'] == 'American Restaurant') ]

Empty DataFrame
Columns: [Neighborhood, American Restaurant, Cluster Labels, Neighborhood Latitude, Neighborhood Longitude, Venue, Venue Latitude, Venue Longitude, Venue Category]
Index: []

In [31]:
#cluster 2
brooklyn_merged.loc[(brooklyn_merged['Cluster Labels'] ==2) & (brooklyn_merged['Venue Category'] == 'American Restaurant') ]

Empty DataFrame
Columns: [Neighborhood, American Restaurant, Cluster Labels, Neighborhood Latitude, Neighborhood Longitude, Venue, Venue Latitude, Venue Longitude, Venue Category]
Index: []

In [32]:
#cluster 3
brooklyn_merged.loc[(brooklyn_merged['Cluster Labels'] ==3) & (brooklyn_merged['Venue Category'] == 'American Restaurant') ]

Neighborhood  American Restaurant  Cluster Labels  Neighborhood Latitude  \
6    Borough Park             0.038462               3              40.633131   
33     Georgetown             0.030303               3              40.623845   
39      Homecrest             0.023256               3              40.598525   
46     Mill Basin             0.023256               3              40.615974   
63  Starrett City             0.066667               3              40.647589   
64    Sunset Park             0.021277               3              40.645103   

    Neighborhood Longitude                  Venue  Venue Latitude  \
6               -73.990498               Orchidea       40.636390   
33              -73.916075          Gourmet Grill       40.619543   
39              -73.959185  Three Star Restaurant       40.599043   
46              -73.915154          Gourmet Grill       40.619543   
63              -73.879370          Boston Market       40.647250   
64              -74.010316    George's Restaurant       40.641116   

    Venue Longitude       Venue Category  
6        -73.993899  American Restaurant  
33       -73.916111  American Restaurant  
39       -73.954987  American Restaurant  
46       -73.916111  American Restaurant  
63       -73.882550  American Restaurant  
64       -74.014348  American Restaurant

In [33]:
#cluster 4
brooklyn_merged.loc[(brooklyn_merged['Cluster Labels'] ==4) & (brooklyn_merged['Venue Category'] == 'Italian Restaurant') ]

Empty DataFrame
Columns: [Neighborhood, American Restaurant, Cluster Labels, Neighborhood Latitude, Neighborhood Longitude, Venue, Venue Latitude, Venue Longitude, Venue Category]
Index: []

In [34]:
#cluster 5
brooklyn_merged.loc[(brooklyn_merged['Cluster Labels'] ==5) & (brooklyn_merged['Venue Category'] == 'Italian Restaurant') ]

Empty DataFrame
Columns: [Neighborhood, American Restaurant, Cluster Labels, Neighborhood Latitude, Neighborhood Longitude, Venue, Venue Latitude, Venue Longitude, Venue Category]
Index: []

### OBSERVATION

#### Most of the american restaurants are in cluster 0

##### Cluster 3 represents the neighborhood with the lowest american restaurants. Any entrepreneur should be looking to open a restaurant in Sunset park, Borough Park,Mill Basin or George town. This is advisable due to no competition and massive opportunity for the business to grow.